In [1]:
from math import exp
import numpy as np
import matplotlib.pyplot as plt
import datetime
import sqlite3
import pandas as pd
import hvplot.pandas

from source.portlib import NB_JOURS_ANNEE, get_rendements, get_vol

plt.rcParams['figure.figsize'] = [15, 5]

# Partie 1

## Calibration

In [2]:
data_rate = pd.read_excel('solver.xlsx', sheet_name=1).set_index('DATE')
data_rate.head()

TAUX_OBSERVE         R
DATE                          
0.0001        0.0215  0.020871
0.2500        0.0235  0.022572
0.5000        0.0260  0.023822
0.7500        0.0282  0.027487
1.0000        0.0305  0.031298

In [3]:
data_rate.hvplot()

:NdOverlay   [Variable]
   :Curve   [DATE]   (value)

In [4]:
def courbe_taux(date: float) -> float:
    date = date if date > 0 else 0.0001
    beta_0 = 0.0509387294135403
    beta_1 = -0.0300728704714689
    beta_2 = 0.0198996013841474
    beta_3 = -0.0834749661479616
    tau_0 = 0.109427785737843
    tau_1 = 0.241789711613793
    
    return beta_0 + beta_1 * ((1 - exp(-date / tau_0)) / (date / tau_0)) + beta_2 * (((1 - exp(-date / tau_0)) / (date / tau_0)) - exp(-date / tau_0)) + beta_3 * (((1 - exp(-date / tau_1)) / (date / tau_1)) - exp(-date / tau_1))

In [5]:
test_sample = pd.DataFrame([(i, courbe_taux(i)) for i in np.arange(0, 10, 0.001)]).rename(columns={0: 'DATE', 1: 'VALUE'}).set_index('DATE')
test_sample.hvplot() * data_rate.hvplot(kind='scatter')

:Overlay
   .Curve.I     :Curve   [DATE]   (VALUE)
   .NdOverlay.I :NdOverlay   [Variable]
      :Scatter   [DATE]   (value)

## CPPI

Ici La période est de 01/01/2015 au 12/03/2019. Avec les paramètres suivants:<br>
- Multiplicateur = 3
- Garantie = 100%
- Maturité = 10ans

In [6]:
multiplicateur = 3
garantie = 1
maturite = 10 * NB_JOURS_ANNEE

In [7]:
# Database connexion
conn = sqlite3.connect("../data/findb.s3db")

In [8]:
# SQL Request
data_cac40 = pd.read_sql_query('SELECT date, value FROM time_series as t INNER JOIN instrument as i ON t.instrumentid = i.id WHERE i.name="CAC40"', conn)

# Preprocess
data_cac40['date'] = pd.to_datetime(data_cac40['date']).dt.date
data_cac40 = data_cac40[data_cac40['date'] > datetime.date(2015, 1, 1)]
data_cac40 = data_cac40.set_index('date')

In [9]:
data_cac40.head()

value
date               
2015-01-02  4252.29
2015-01-05  4111.36
2015-01-06  4083.50
2015-01-07  4112.73
2015-01-08  4260.19

In [10]:
data_cac40_list = data_cac40['value'].tolist()
data_cac40_reduced = data_cac40 / data_cac40.shift(1)
data_cac40_recuded_list = data_cac40_reduced['value'].tolist()

In [11]:
# Réplication

length = data_cac40.shape[0]

s = [0] * length
s[0] = 1

for i in range(1, length):
    s[i] = s[i - 1] * (data_cac40_recuded_list[i])

In [12]:
pd.DataFrame(s, columns=['VALUE']).hvplot()

:Curve   [index]   (VALUE)

In [13]:
def discount_factor(t_0: int, grand_t: int) -> float:
    x = (1 + courbe_taux(grand_t))**grand_t
    y = (1 + courbe_taux(t_0))**(-t_0)
    return y/x

In [14]:
# Création des variables
nav = [0] * length
ar = [0] * length
bondfloor = [0] * length
coussin = [0] * length
expo = [0] * length
nav_rendement = [0] * length
s_rendement = [0] * length

# Initialisation : t = 0
nav[0] = 1
bondfloor[0] = garantie * discount_factor(0, maturite/NB_JOURS_ANNEE)# exp(-courbe_taux(0)*maturite/NB_JOURS_ANNEE)
coussin[0] = nav[0] - bondfloor[0]
ar[0] = multiplicateur * coussin[0]
expo[0] = ar[0] / nav[0]

In [15]:
# Calcul des variables

for i in range(0, length - 1):
    nav[i + 1] = ar[i] * s[i + 1]/s[i] + (nav[i] - ar[i]) * (1 + courbe_taux(i/NB_JOURS_ANNEE) * 1/NB_JOURS_ANNEE)
    bondfloor[i + 1] = garantie * discount_factor(i/NB_JOURS_ANNEE, maturite/NB_JOURS_ANNEE)# exp(-courbe_taux(i/NB_JOURS_ANNEE)*(maturite-i)/NB_JOURS_ANNEE)
    coussin[i + 1] = nav[i + 1] - bondfloor[i + 1]
    ar[i + 1] = multiplicateur * coussin[i + 1]
    expo[i + 1] = ar[i + 1] / nav[i + 1]
    nav_rendement[i + 1] = nav[i + 1] / nav[i] - 1
    s_rendement[i + 1] = s[i + 1] / s[i] - 1

In [16]:
data_nav_cac40 = pd.DataFrame({
    'NAV' : nav,
    'Sous-jacent': s,
    'Bondfloor': bondfloor,
    'Exposition': expo
})

In [17]:
data_nav_cac40.hvplot()

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [18]:
get_rendements(nav, s)

3M        6M        1Y        3Y       ALL
NAV                  0.134969 -0.094851 -0.039083  0.099740  0.051469
NAV Annualisé        0.634705 -0.175868 -0.039083  0.032199  0.011915
Benchmark            0.102457 -0.041489  0.007049  0.191292  0.239391
Benchmark Annualisé  0.460298 -0.078953  0.007049  0.060082  0.051957

In [19]:
get_vol(nav_rendement, s_rendement)

Vol. Annualisé
NAV              0.003215
Benchmark        0.001918

In [20]:
print(f'Coussin : {coussin[0]}\nExpo 0 : {expo[0]}\nExpo moy : {np.mean(expo)}')

Coussin : 0.379079971184746
Expo 0 : 1.1372399135542381
Expo moy : 1.3849677030493266


## Garantie Max NAV

In [21]:
def clean_df_ts(df: pd.DataFrame) -> pd.DataFrame:
    df['date'] = pd.to_datetime(df['date']).dt.date
    # df = df[df['date'] > datetime.date(2015, 1, 1)]
    return df.set_index('date')

In [22]:
data_eurostoxx = pd.read_sql_query('SELECT date, value FROM time_series as t INNER JOIN instrument as i ON t.instrumentid = i.id WHERE i.name="EUROSTOXX50"', conn)
data_sp500 = pd.read_sql_query('SELECT date, value FROM time_series as t INNER JOIN instrument as i ON t.instrumentid = i.id WHERE i.name="S&P500"', conn)
data_msciw = pd.read_sql_query('SELECT date, value FROM time_series as t INNER JOIN instrument as i ON t.instrumentid = i.id WHERE i.name="MSCI WORLD"', conn)

In [23]:
data_eurostoxx = clean_df_ts(data_eurostoxx)
data_sp500 = clean_df_ts(data_sp500)
data_msciw = clean_df_ts(data_msciw)

In [24]:
data_eurostoxx.hvplot() * data_sp500.hvplot() * data_msciw.hvplot()

:Overlay
   .Curve.I   :Curve   [date]   (value)
   .Curve.II  :Curve   [date]   (value)
   .Curve.III :Curve   [date]   (value)

In [25]:
def get_ts_reduced(df: pd.DataFrame):
    df = df / df.shift(1)
    return df['value'].tolist()

In [26]:
data_eurostoxx_reduced = get_ts_reduced(data_eurostoxx)
data_sp500_reduced = get_ts_reduced(data_sp500)
data_msciw_reduced = get_ts_reduced(data_msciw)

In [27]:
len(data_msciw_reduced)

5007

In [28]:
length = min(len(data_eurostoxx_reduced), len(data_sp500_reduced), len(data_msciw_reduced))

# Actions
s1 = [0] * length
s2 = [0] * length
s3 = [0] * length
s1[0], s2[0], s3[0] = 1, 1, 1

# Portefeuille
port = [0] * length
port[0] = 1

for i in range(1, length):
    s1[i] = s1[i - 1] * (data_eurostoxx_reduced[i])
    s2[i] = s2[i - 1] * (data_sp500_reduced[i])
    s3[i] = s3[i - 1] * (data_msciw_reduced[i])
    
    port[i] = 0.25 * s1[i] + 0.25 * s2[i] + 0.5 * s3[i]

In [29]:
(pd.DataFrame(port).hvplot() * 
 pd.DataFrame(s1).hvplot() * 
 pd.DataFrame(s2).hvplot() *
 pd.DataFrame(s3).hvplot())

:Overlay
   .Curve.I   :Curve   [index]   (0)
   .Curve.II  :Curve   [index]   (0)
   .Curve.III :Curve   [index]   (0)
   .Curve.IV  :Curve   [index]   (0)

In [30]:
def garantie_max(nav):
    x = 1
    y = 0.85
    return max(y * np.max(nav), x)

In [31]:
# Création des variables
nav = [0] * length
ar = [0] * length
bondfloor = [0] * length
coussin = [0] * length
expo = [0] * length
nav_rendement = [0] * length
port_rendement = [0] * length

gar = [0] * length

# Initialisation : t = 0
nav[0] = 1
bondfloor[0] = garantie_max(nav) * discount_factor(0, maturite/NB_JOURS_ANNEE)# exp(-courbe_taux(0)*maturite/NB_JOURS_ANNEE)
coussin[0] = nav[0] - bondfloor[0]
ar[0] = multiplicateur * coussin[0]
expo[0] = ar[0] / nav[0]

gar[0] = garantie_max(nav)

In [32]:
# Calcul des variables

for i in range(0, length - 1):
    nav[i + 1] = ar[i] * port[i + 1]/port[i] + (nav[i] - ar[i]) * (1 + courbe_taux(i/NB_JOURS_ANNEE) * 1/NB_JOURS_ANNEE)
    gar[i] = garantie_max(nav)
    bondfloor[i + 1] = garantie_max(nav) * discount_factor(i/NB_JOURS_ANNEE, maturite/NB_JOURS_ANNEE)# exp(-courbe_taux(i/NB_JOURS_ANNEE)*(maturite-i)/NB_JOURS_ANNEE)
    coussin[i + 1] = nav[i + 1] - bondfloor[i + 1]
    ar[i + 1] = multiplicateur * coussin[i + 1]
    expo[i + 1] = ar[i + 1] / nav[i + 1]
    nav_rendement[i + 1] = nav[i + 1] / nav[i] - 1
    port_rendement[i + 1] = port[i + 1] / port[i] - 1

In [33]:
data_nav_indices = pd.DataFrame({
    'NAV' : nav,
    'Sous-jacent': port,
    'Bondfloor': bondfloor,
    'Exposition': expo
})

In [34]:
data_nav_indices.hvplot()

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [35]:
get_rendements(nav, port)

3M        6M        1Y        3Y       ALL
NAV                  0.009825 -0.040560  0.030322  0.324530  0.945725
NAV Annualisé        0.038684 -0.077221  0.030322  0.098215  0.035511
Benchmark            0.013053  0.002462  0.045985  0.245164  0.676473
Benchmark Annualisé  0.051629  0.004785  0.045985  0.075826  0.027457

In [36]:
get_vol(nav_rendement, port_rendement)

Vol. Annualisé
NAV              0.001295
Benchmark        0.000752

In [37]:
print(f'Coussin : {coussin[0]}\nExpo 0 : {expo[0]}\nExpo moy : {np.mean(expo)}')

Coussin : 0.379079971184746
Expo 0 : 1.1372399135542381
Expo moy : 1.5092694194108192
